## Initial installs and imports


In [1]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import plotly.io as pio
import polars as pl
from numpy.typing import NDArray
from plotly.graph_objs._figure import Figure
from plotly.subplots import make_subplots
from polars import DataFrame
from polars.dataframe.frame import DataFrame
from pyod.models.knn import KNN
from scipy.stats import ks_2samp
from catboost.core import CatBoostClassifier
from sklearn.metrics import confusion_matrix
from lightgbm.sklearn import LGBMClassifier
from polars.dataframe.frame import DataFrame
from skimpy import skim
from sklearn.neighbors._classification import KNeighborsClassifier
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.model_selection import RepeatedStratifiedKFold
from tpot import TPOTClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from mlxtend.classifier import StackingClassifier
from tpot import TPOTClassifier
from sklearn.model_selection import train_test_split
from sklearn.base import clone
from catboost import CatBoostClassifier
from xgboost import XGBClassifier
from sklearn.semi_supervised import LabelSpreading
from sklearn.metrics import accuracy_score
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import warnings

In [2]:
# Define file paths within colab
train_csv = "train.csv"
test_csv = "test.csv"
pio.templates.default = "simple_white"
warnings.filterwarnings("ignore")

In [3]:
from spaceship_functions import (
    make_subplot,
    create_encoder_mapping,
    encode_feature,
    mark_outliers,
    iterative_duplicate_check,
    polars_crosstab,
    calculate_chi2,
    int_range,
    skopt_bayesian_search,
    conduct_PCA,
    split_cabin_column,
    calculate_model_statistics
)

In [4]:
train: DataFrame = pl.read_csv(train_csv)
test: DataFrame = pl.read_csv(test_csv)

train = train.select(
    pl.all().name.map(lambda col_name: col_name.lower())
).with_row_index()

test = test.select(
    pl.all().name.map(lambda col_name: col_name.lower())
).with_row_index()

train.sample(5)

shape: (5, 15)
┌───────┬─────────────┬────────────┬───────────┬───┬────────┬────────┬───────────────┬─────────────┐
│ index ┆ passengerid ┆ homeplanet ┆ cryosleep ┆ … ┆ spa    ┆ vrdeck ┆ name          ┆ transported │
│ ---   ┆ ---         ┆ ---        ┆ ---       ┆   ┆ ---    ┆ ---    ┆ ---           ┆ ---         │
│ u32   ┆ str         ┆ str        ┆ bool      ┆   ┆ f64    ┆ f64    ┆ str           ┆ bool        │
╞═══════╪═════════════╪════════════╪═══════════╪═══╪════════╪════════╪═══════════════╪═════════════╡
│ 4310  ┆ 4594_01     ┆ Europa     ┆ false     ┆ … ┆ 3001.0 ┆ 127.0  ┆ Tabius Folhal ┆ false       │
│ 5907  ┆ 6264_01     ┆ Earth      ┆ false     ┆ … ┆ 0.0    ┆ 680.0  ┆ Thery Rodger  ┆ false       │
│ 5408  ┆ 5776_01     ┆ Earth      ┆ false     ┆ … ┆ 4.0    ┆ 383.0  ┆ Luise Saundez ┆ false       │
│ 4167  ┆ 4449_01     ┆ Mars       ┆ false     ┆ … ┆ 31.0   ┆ 26.0   ┆ Tyog Cla      ┆ true        │
│ 349   ┆ 0383_02     ┆ Earth      ┆ true      ┆ … ┆ 0.0    ┆ 0.0    ┆ Evane         ┆ false       │
│       ┆             ┆            ┆           ┆   ┆        ┆        ┆ Wagnerray     ┆             │
└───────┴─────────────┴────────────┴───────────┴───┴────────┴────────┴───────────────┴─────────────┘

In [5]:
test.sample(5)

shape: (5, 14)
┌───────┬─────────────┬────────────┬───────────┬───┬──────────────┬─────┬────────┬─────────────────┐
│ index ┆ passengerid ┆ homeplanet ┆ cryosleep ┆ … ┆ shoppingmall ┆ spa ┆ vrdeck ┆ name            │
│ ---   ┆ ---         ┆ ---        ┆ ---       ┆   ┆ ---          ┆ --- ┆ ---    ┆ ---             │
│ u32   ┆ str         ┆ str        ┆ bool      ┆   ┆ f64          ┆ f64 ┆ f64    ┆ str             │
╞═══════╪═════════════╪════════════╪═══════════╪═══╪══════════════╪═════╪════════╪═════════════════╡
│ 2017  ┆ 4341_01     ┆ Earth      ┆ false     ┆ … ┆ 793.0        ┆ 0.0 ┆ 0.0    ┆ Tance Simson    │
│ 2555  ┆ 5588_02     ┆ Mars       ┆ true      ┆ … ┆ 0.0          ┆ 0.0 ┆ 0.0    ┆ Cobix Cola      │
│ 463   ┆ 0963_01     ┆ Europa     ┆ true      ┆ … ┆ 0.0          ┆ 0.0 ┆ 0.0    ┆ Izares Syncepul │
│ 238   ┆ 0497_01     ┆ Mars       ┆ true      ┆ … ┆ 0.0          ┆ 0.0 ┆ 0.0    ┆ Muebix Mepie    │
│ 2512  ┆ 5495_01     ┆ Mars       ┆ true      ┆ … ┆ 0.0          ┆ 0.0 ┆ 0.0    ┆ Clow Blité      │
└───────┴─────────────┴────────────┴───────────┴───┴──────────────┴─────┴────────┴─────────────────┘

In [6]:
skim(train)

╭──────────────────────────────────────────────── skimpy summary ─────────────────────────────────────────────────╮
│          Data Summary                Data Types                                                                 │
│ ┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━┓ ┏━━━━━━━━━━━━━┳━━━━━━━┓                                                          │
│ ┃ dataframe         ┃ Values ┃ ┃ Column Type ┃ Count ┃                                                          │
│ ┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━┩ ┡━━━━━━━━━━━━━╇━━━━━━━┩                                                          │
│ │ Number of rows    │ 8693   │ │ float64     │ 6     │                                                          │
│ │ Number of columns │ 15     │ │ string      │ 5     │                                                          │
│ └───────────────────┴────────┘ │ bool        │ 3     │                                                          │
│                                │ int64       │ 1     │                                                          │
│                                └─────────────┴───────┘                                                          │
│                                                     number                                                      │
│ ┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━┳━━━━━━━━┳━━━━━━━━━┳━━━━━━━━━┳━━━━━┳━━━━━━━━┳━━━━━━━━┳━━━━━━━━┳━━━━━━━━┳━━━━━━━━━┓  │
│ ┃ column_name       ┃ NA    ┃ NA %   ┃ mean    ┃ sd      ┃ p0  ┃ p25    ┃ p50    ┃ p75    ┃ p100   ┃ hist    ┃  │
│ ┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━╇━━━━━━━━╇━━━━━━━━━╇━━━━━━━━━╇━━━━━╇━━━━━━━━╇━━━━━━━━╇━━━━━━━━╇━━━━━━━━╇━━━━━━━━━┩  │
│ │ index             │     0 │      0 │    4346 │    2510 │   0 │   2173 │   4346 │   6519 │   8692 │ ▇▇▇▇▇▇  │  │
│ │ age               │   179 │   2.06 │   28.83 │   14.49 │   0 │     19 │     27 │     38 │     79 │  ▂▇▆▃▁  │  │
│ │ roomservice       │   181 │   2.08 │   224.7 │   666.7 │   0 │      0 │      0 │     47 │  14330 │    ▇    │  │
│ │ foodcourt         │   183 │   2.11 │   458.1 │    1611 │   0 │      0 │      0 │     76 │  29810 │    ▇    │  │
│ │ shoppingmall      │   208 │   2.39 │   173.7 │   604.7 │   0 │      0 │      0 │     27 │  23490 │    ▇    │  │
│ │ spa               │   183 │   2.11 │   311.1 │    1137 │   0 │      0 │      0 │     59 │  22410 │    ▇    │  │
│ │ vrdeck            │   188 │   2.16 │   304.9 │    1146 │   0 │      0 │      0 │     46 │  24130 │    ▇    │  │
│ └───────────────────┴───────┴────────┴─────────┴─────────┴─────┴────────┴────────┴────────┴────────┴─────────┘  │
│                                                      bool                                                       │
│ ┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━┓  │
│ ┃ column_name                        ┃ true            ┃ true rate                     ┃ hist                ┃  │
│ ┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━┩  │
│ │ cryosleep                          │            3037 │                          0.35 │       ▇    ▅        │  │
│ │ vip                                │             199 │                         0.023 │          ▇          │  │
│ │ transported                        │            4378 │                           0.5 │       ▇    ▇        │  │
│ └────────────────────────────────────┴─────────────────┴───────────────────────────────┴─────────────────────┘  │
│                                                     string                                                      │
│ ┏━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━┓  │
│ ┃ column_name              ┃ NA       ┃ NA %       ┃ words per row                ┃ total words              ┃  │
│ ┡━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━┩  │
│ │ passengerid              │        0 │          0 │  

In [7]:
skim(test)

╭──────────────────────────────────────────────── skimpy summary ─────────────────────────────────────────────────╮
│          Data Summary                Data Types                                                                 │
│ ┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━┓ ┏━━━━━━━━━━━━━┳━━━━━━━┓                                                          │
│ ┃ dataframe         ┃ Values ┃ ┃ Column Type ┃ Count ┃                                                          │
│ ┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━┩ ┡━━━━━━━━━━━━━╇━━━━━━━┩                                                          │
│ │ Number of rows    │ 4277   │ │ float64     │ 6     │                                                          │
│ │ Number of columns │ 14     │ │ string      │ 5     │                                                          │
│ └───────────────────┴────────┘ │ bool        │ 2     │                                                          │
│                                │ int64       │ 1     │                                                          │
│                                └─────────────┴───────┘                                                          │
│                                                     number                                                      │
│ ┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━┳━━━━━━━━┳━━━━━━━━━┳━━━━━━━━━┳━━━━━┳━━━━━━━━┳━━━━━━━━┳━━━━━━━━┳━━━━━━━━┳━━━━━━━━━┓  │
│ ┃ column_name       ┃ NA    ┃ NA %   ┃ mean    ┃ sd      ┃ p0  ┃ p25    ┃ p50    ┃ p75    ┃ p100   ┃ hist    ┃  │
│ ┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━╇━━━━━━━━╇━━━━━━━━━╇━━━━━━━━━╇━━━━━╇━━━━━━━━╇━━━━━━━━╇━━━━━━━━╇━━━━━━━━╇━━━━━━━━━┩  │
│ │ index             │     0 │      0 │    2138 │    1235 │   0 │   1069 │   2138 │   3207 │   4276 │ ▇▇▇▇▇▇  │  │
│ │ age               │    91 │   2.13 │   28.66 │   14.18 │   0 │     19 │     26 │     37 │     79 │  ▂▇▅▃▁  │  │
│ │ roomservice       │    82 │   1.92 │   219.3 │     607 │   0 │      0 │      0 │     53 │  11570 │    ▇    │  │
│ │ foodcourt         │   106 │   2.48 │   439.5 │    1528 │   0 │      0 │      0 │     78 │  25270 │    ▇    │  │
│ │ shoppingmall      │    98 │   2.29 │   177.3 │   560.8 │   0 │      0 │      0 │     33 │   8292 │    ▇    │  │
│ │ spa               │   101 │   2.36 │   303.1 │    1117 │   0 │      0 │      0 │     50 │  19840 │    ▇    │  │
│ │ vrdeck            │    80 │   1.87 │   310.7 │    1247 │   0 │      0 │      0 │     36 │  22270 │    ▇    │  │
│ └───────────────────┴───────┴────────┴─────────┴─────────┴─────┴────────┴────────┴────────┴────────┴─────────┘  │
│                                                      bool                                                       │
│ ┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━┓  │
│ ┃ column_name                        ┃ true            ┃ true rate                     ┃ hist                ┃  │
│ ┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━┩  │
│ │ cryosleep                          │            1544 │                          0.36 │       ▇    ▅        │  │
│ │ vip                                │              74 │                         0.017 │          ▇          │  │
│ └────────────────────────────────────┴─────────────────┴───────────────────────────────┴─────────────────────┘  │
│                                                     string                                                      │
│ ┏━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━┓  │
│ ┃ column_name              ┃ NA       ┃ NA %       ┃ words per row                ┃ total words              ┃  │
│ ┡━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━┩  │
│ │ passengerid              │        0 │          0 │                            1 │                     4277 │  │
│ │ homeplanet               │       87 │       2.03 │  

Both datasets have a decent number of missing values across the variables, which we should dive into further. Let's start there before we dive into univariate analysis and a closer look at our target variable.

#### Are name and passenger_id unique identifiers in these datasets?

In [8]:
if len(train["name"].unique()) == train.shape[0]:
    print("All passenger names are unique identifiers of passengers aboard vessel.")

if len(train["passengerid"].unique()) == train.shape[0]:
    print("Passenger id is a unique identifier for passengers aboard vessel.")

Passenger id is a unique identifier for passengers aboard vessel.


Passenger ids are unique, however names are not, so we'll use passengerid as our primary key for passengers in the rest of our analysis.

## Duplicate Analysis

In [9]:
print(f"Polars: {train.is_duplicated().sum()} duplicates found in train.")
print(f"Polars: {test.is_duplicated().sum()} duplicates found in test.\n")

print(f"Pandas: {train.to_pandas().duplicated().sum()} duplicates found in train.")
print(f"Pandas: {test.to_pandas().duplicated().sum()} duplicates found in test.")

Polars: 0 duplicates found in train.
Polars: 0 duplicates found in test.

Pandas: 0 duplicates found in train.
Pandas: 0 duplicates found in test.


Using an inital pass at the built-in pandas and polars methods for duplicate detection, we can see that there are none in train and test sets. We can also iteratively check for duplicates using expanding subsets of features to verify this conclusion.


In [10]:
train.to_pandas().columns

Index(['index', 'passengerid', 'homeplanet', 'cryosleep', 'cabin',
       'destination', 'age', 'vip', 'roomservice', 'foodcourt', 'shoppingmall',
       'spa', 'vrdeck', 'name', 'transported'],
      dtype='object')

In [11]:
iterative_duplicate_check(train)

0 duplicates ['passengerid']
0 duplicates ['passengerid', 'homeplanet']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination', 'age']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination', 'age', 'vip']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination', 'age', 'vip', 'roomservice']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination', 'age', 'vip', 'roomservice', 'foodcourt']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination', 'age', 'vip', 'roomservice', 'foodcourt', 'shoppingmall']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination', 'age', 'vip', 'roomservice', 'foodcourt', 'shoppingmall', 'spa']
0 duplicates ['passengerid', 'ho

In [12]:
iterative_duplicate_check(test)

0 duplicates ['passengerid']
0 duplicates ['passengerid', 'homeplanet']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination', 'age']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination', 'age', 'vip']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination', 'age', 'vip', 'roomservice']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination', 'age', 'vip', 'roomservice', 'foodcourt']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination', 'age', 'vip', 'roomservice', 'foodcourt', 'shoppingmall']
0 duplicates ['passengerid', 'homeplanet', 'cryosleep', 'cabin', 'destination', 'age', 'vip', 'roomservice', 'foodcourt', 'shoppingmall', 'spa']
0 duplicates ['passengerid', 'ho

From this printout we can see that we're getting zero duplicates across the board, for multiple subsets of columns in both datasets. Let's move on to null values!

## Null values

In [13]:
train.null_count()

shape: (1, 15)
┌───────┬─────────────┬────────────┬───────────┬───┬─────┬────────┬──────┬─────────────┐
│ index ┆ passengerid ┆ homeplanet ┆ cryosleep ┆ … ┆ spa ┆ vrdeck ┆ name ┆ transported │
│ ---   ┆ ---         ┆ ---        ┆ ---       ┆   ┆ --- ┆ ---    ┆ ---  ┆ ---         │
│ u32   ┆ u32         ┆ u32        ┆ u32       ┆   ┆ u32 ┆ u32    ┆ u32  ┆ u32         │
╞═══════╪═════════════╪════════════╪═══════════╪═══╪═════╪════════╪══════╪═════════════╡
│ 0     ┆ 0           ┆ 201        ┆ 217       ┆ … ┆ 183 ┆ 188    ┆ 200  ┆ 0           │
└───────┴─────────────┴────────────┴───────────┴───┴─────┴────────┴──────┴─────────────┘

In [14]:
test.null_count()

shape: (1, 14)
┌───────┬─────────────┬────────────┬───────────┬───┬──────────────┬─────┬────────┬──────┐
│ index ┆ passengerid ┆ homeplanet ┆ cryosleep ┆ … ┆ shoppingmall ┆ spa ┆ vrdeck ┆ name │
│ ---   ┆ ---         ┆ ---        ┆ ---       ┆   ┆ ---          ┆ --- ┆ ---    ┆ ---  │
│ u32   ┆ u32         ┆ u32        ┆ u32       ┆   ┆ u32          ┆ u32 ┆ u32    ┆ u32  │
╞═══════╪═════════════╪════════════╪═══════════╪═══╪══════════════╪═════╪════════╪══════╡
│ 0     ┆ 0           ┆ 87         ┆ 93        ┆ … ┆ 98           ┆ 101 ┆ 80     ┆ 94   │
└───────┴─────────────┴────────────┴───────────┴───┴──────────────┴─────┴────────┴──────┘

Both sets have null values across most of the features. Thankfully transported isn't missing any in the training set, given that it is not included in the test set. We'll need to impute these null values before we start modeling. Let's proceed now to the shape of our features individually.

### Univariate analysis

In [15]:
fig1: Figure = make_subplots(
    rows=1,
    cols=5,
    subplot_titles=("Home Planet", "Cryo-sleep", "Destination", "VIP", "Transported"),
)


for column, feature in enumerate(
    ["homeplanet", "cryosleep", "destination", "vip", "transported"]
):
    make_subplot(fig1, train, feature, [1, column + 1], "blue")

fig1.update_yaxes(title_text="Observations", row=1, col=1)
fig1.update_layout(
    title_text="Training set - categorical/boolean feature balancing",
    height=325,
    showlegend=False,
)
fig1.show()


fig2: Figure = make_subplots(
    rows=1, cols=5, subplot_titles=("Home Planet", "Cryo-sleep", "Destination", "VIP")
)

for column, feature in enumerate(["homeplanet", "cryosleep", "destination", "vip"]):
    make_subplot(fig2, test, feature, [1, column + 1], "purple")

fig2.update_yaxes(title_text="Observations", row=1, col=1)
fig2.update_layout(
    title_text="Testing set - categorical/boolean feature balancing",
    height=325,
    showlegend=False,
)
fig2.show()

The above graph set shows that class proportions across each set of categorical features are consistent, even though the test set is naturally smaller. The main difference betwee train and test sets is that the training set has the transported target feature, whereas the test set does not. Let's look at our features corresponding to each passenger's expenditure on amenities.

In [16]:
fig: Figure = make_subplots(
    rows=2,
    cols=5,
    subplot_titles=(
        "Room Service",
        "Food Court",
        "Shopping Mall",
        "Spa",
        "VR Deck",
        "Room Service",
        "Food Court",
        "Shopping Mall",
        "Spa",
        "VR Deck",
    ),
)

spending: list[str] = ["roomservice", "foodcourt", "shoppingmall", "spa", "vrdeck"]

for i, feature in enumerate(spending):
    fig.add_trace(
        go.Scatter(
            x=train["index"],
            y=train[feature],
            mode="markers",
            marker=dict(color=train[feature], colorscale="Blues_r"),
        ),
        row=1,
        col=i + 1,
    )

    fig.add_trace(
        go.Scatter(
            x=test["index"],
            y=test[feature],
            mode="markers",
            marker=dict(color=test[feature], colorscale="AgSunset"),
        ),
        row=2,
        col=i + 1,
    )

    fig.update_xaxes(title_text="Passengers", row=1, col=i + 1)
    fig.update_xaxes(title_text="Passengers", row=2, col=i + 1)

fig.update_yaxes(title_text="Training set spending", row=1, col=1)
fig.update_yaxes(title_text="Testing set spending", row=2, col=1)
fig.update_layout(
    title_text="Expenditures on amenities in datasets",
    height=550,
    showlegend=False,
)

fig.show()

When looking at passenger-level spending on amenities aboard the ship, we can see that multiple features have a much higher dispersion within the test when compared to the homologous feature in the training set. Let's also break out the cabin feature into deck, cabin number and side so that we have more data to work with since those details could be useful when we check for correlations or other patterns later.

In [17]:
from polars.dataframe.frame import DataFrame

train: DataFrame = split_cabin_column(train)
test: DataFrame = split_cabin_column(test)

## EDA Hypotheses
In this section we'll make some assumptions about our data, digging into the train and test sets further. I'll state the hypothesis up-front, conduct some analysis and then decide on what action(s) we'll take, if any.

### Hypothesis 1: We have a no outliers in both datasets.
#### <u>KNN anomaly detection</u>
First we'll prep our data before running KNN analysis on each dataset.

In [18]:
train_num: DataFrame = train.drop(["index", "passengerid", "name"])
test_num: DataFrame = test.drop(
    [
        "index",
        "passengerid",
        "name",
    ]
)

encoder_mapping_key = dict()
for col in train_num.columns:
    try:
        key: dict[str, int] = create_encoder_mapping(train_num, col)
        train_num = encode_feature(train_num, col, key)
        test_num = encode_feature(test_num, col, key)
        encoder_mapping_key[col] = key
    except:
        pass

x_train: DataFrame = train_num.drop("transported").to_numpy()
x_test: DataFrame = test_num.to_numpy()
y: DataFrame = train_num["transported"].to_numpy()

# Scale data
scaled_xtrain: NDArray = StandardScaler().fit_transform(x_train)
scaled_xtest: NDArray = StandardScaler().fit_transform(x_test)

# Fill nan values in place
np.nan_to_num(scaled_xtrain, copy=False, nan=0.0)
np.nan_to_num(scaled_xtest, copy=False, nan=0.0)

# Create training and validation sets to use for modeling
training_x, validation_x, training_y, validation_y = train_test_split(
    scaled_xtrain, y, test_size=0.3, random_state=15, stratify=y
)

In [19]:
knn_train: NDArray = KNN(contamination=0.1, method="mean", n_neighbors=5).fit(
    scaled_xtrain
)
knn_test: NDArray = KNN(contamination=0.1, method="mean", n_neighbors=5).fit(
    scaled_xtest
)

train_predicted = pd.Series(knn_train.predict(scaled_xtrain))
test_predicted = pd.Series(knn_test.predict(scaled_xtest))

print("KNN threshold - train:", knn_train.threshold_)
print("KNN threshold - test:", knn_test.threshold_, "\n")

print(
    f"Train set outliers = {train_predicted.sum()}, {round((train_predicted.sum()/len(train_predicted)),4):%} of data"
)
print(
    f"Test set outliers = {test_predicted.sum()}, {round(test_predicted.sum()/len(test_predicted),4):%} of data"
)

train_decision_scores = pd.DataFrame(knn_train.decision_scores_, columns=["scores"])
test_decision_scores = pd.DataFrame(knn_test.decision_scores_, columns=["scores"])

KNN threshold - train: 1.9075906653691
KNN threshold - test: 1.8921065083332287 

Train set outliers = 352, 4.050000% of data
Test set outliers = 210, 4.910000% of data


This is a small number of outliers in both datasets when assessed as a proportion of the overall dataset sizes. Let's look at the points graphically to get a better sense of the spread.

In [20]:
outlier_plot = go.Figure()

scores: list[float] = [train_decision_scores.scores, test_decision_scores.scores]
names: list[str] = ["Training data", "Testing data"]
colors: list[str] = [
    "rgb(5, 121, 199)",
    "rgb(82, 3, 162)",
]

for i, series in enumerate(scores):
    outlier_plot.add_trace(go.Box(x=series, name=names[i], marker_color=colors[i]))
outlier_plot.update_layout(
    title_text="Decision Score Box Plots by dataset", height=400, width=1000
)

outlier_plot.show()

Our hypothesis was incorrect--though both datafiles have equally dense data in the interquartile range, we have a significant number of outliers with a pretty huge spread. For our purposes here, we'll designate any decision score above the box plot's upper limit as an outlier, marking those observations in our data for further analysis.

In [21]:
from pandas.core.frame import DataFrame

train_outliers: DataFrame = train_decision_scores[
    train_decision_scores.scores > 1.49053
]
test_outliers: DataFrame = test_decision_scores[test_decision_scores.scores > 1.78353]
train: DataFrame = mark_outliers(train, train_outliers.index)
test: DataFrame = mark_outliers(test, test_outliers.index)

## Hypothesis 2: Outliers are more likely to be saved from the spaceship titanic.
Now that we have our outliers in both sets marked, we should cross-tabulate them against transported. However since we do not have transported data for the test set, let's do a hypothesis test to test the assumption that our training and testing set outlier data can be treated as arising from the same distribution, and thus being interchangeable in this instance. Said another way, assuming that our training set outliers are more likely to be positive for transported, would we statistically be able to infer that to be also true for the test set without having empirical transported data in the test set on-hand?

Once we know the answer to this question, we can see if it's would be statistically reasonable to extend our conclusions from the training data cross-tab to the test set as well.

In the Kolmogorov-Smirnov test:

<center>

$H_0$ = Training and test outliers come from the same underlying distribution.<br>
$H_1$ = Training and test outliers do not come from the same underlying distribution.
</center>



In [22]:
train_outlier_df: DataFrame = train.filter(pl.col("outliers") == 1).to_numpy()
test_outlier_df: DataFrame = test.filter(pl.col("outliers") == 1).to_numpy()

stat, p_value = ks_2samp(train_outliers, test_outliers)

if p_value[0] < 0.05:
    print(
        "We reject the null hypothesis, test and training outliers do not come from the same distribution."
    )
else:
    print(
        "We reject the null hypothesis, training and test outliers are sample from the same distribution."
    )

We reject the null hypothesis, test and training outliers do not come from the same distribution.


Since the rejected the null hypothesis, we'll only be able to make statements about the training set and its relationship to the dependent variable. Let's cross-tabulate that dataframe now.

In [23]:
polars_crosstab(train, "transported", "outliers")

shape: (2, 3)
┌──────────┬───────┬──────┐
│ outliers ┆ false ┆ true │
│ ---      ┆ ---   ┆ ---  │
│ i64      ┆ i64   ┆ i64  │
╞══════════╪═══════╪══════╡
│ 0        ┆ 3133  ┆ 3826 │
│ 1        ┆ 1182  ┆ 552  │
└──────────┴───────┴──────┘

#### Chi-squared test of independence:

$H_0$ = The transported and outliers are statistically independent of each other <br>
$H_1$ = The  transported and outliers are not statistically independent of each other

In [24]:
p_value: float = calculate_chi2(train, "transported", "outliers")

if p_value < 0.05:
    print(
        f"We reject the null hypothesis, transported and outliers are not independent. p-value = {p_value:.2e}"
    )

print(
    f"Transported - outliers correlation = {np.round(train[['transported','outliers']].corr().to_numpy()[0,1],4)}"
)

We reject the null hypothesis, transported and outliers are not independent. p-value = 3.61e-66
Transported - outliers correlation = -0.185


Between the cross tab dataframe and our hypothesis testing, we can see that there isn't a obvious relationship between outliers and the dependent variable, however there is still a statistically significant lack of independence between the two variables. Let's see if there are any other correlations that jump out when we zoom out and look at all of the variables rather than just these two in isolation.

## Hypothesis 2: Correlations are similar between the training and testing datasets
### Correlations

Let's start by correlating the respective correlation matrices in train and test.

In [25]:
corr: DataFrame = train_num.to_pandas().corr()
corr

homeplanet  cryosleep  destination       age       vip  \
homeplanet      1.000000   0.068726    -0.131847  0.035512  0.099874   
cryosleep       0.068726   1.000000     0.075796  0.046974 -0.062440   
destination    -0.131847   0.075796     1.000000 -0.023706  0.018930   
age             0.035512   0.046974    -0.023706  1.000000  0.028508   
vip             0.099874  -0.062440     0.018930  0.028508  1.000000   
roomservice     0.167727  -0.281613    -0.070650 -0.058789  0.041684   
foodcourt      -0.001270  -0.285576    -0.004616 -0.011082  0.106862   
shoppingmall    0.088515  -0.273230    -0.041570 -0.063396  0.013401   
spa             0.013129  -0.287232    -0.023296 -0.020650  0.058091   
vrdeck         -0.024995  -0.284654     0.005003 -0.033788  0.082087   
transported    -0.107755  -0.404716    -0.059439 -0.056009  0.032360   
deck            0.230194   0.050019     0.013535  0.059463  0.138708   
cabin_num      -0.187816  -0.058838     0.003495 -0.095498 -0.075954   
side            0.001179   0.001450     0.000383 -0.018635  0.009381   

              roomservice  foodcourt  shoppingmall       spa    vrdeck  \
homeplanet       0.167727  -0.001270      0.088515  0.013129 -0.024995   
cryosleep       -0.281613  -0.285576     -0.273230 -0.287232 -0.284654   
destination     -0.070650  -0.004616     -0.041570 -0.023296  0.005003   
age             -0.058789  -0.011082     -0.063396 -0.020650 -0.033788   
vip              0.041684   0.106862      0.013401  0.058091  0.082087   
roomservice      1.000000  -0.026903      0.149248  0.006387 -0.014351   
foodcourt       -0.026903   1.000000     -0.000824  0.246973  0.271933   
shoppingmall     0.149248  -0.000824      1.000000  0.029182 -0.015386   
spa              0.006387   0.246973      0.029182  1.000000  0.200716   
vrdeck          -0.014351   0.271933     -0.015386  0.200716  1.000000   
transported      0.272828   0.044451      0.078103  0.282438  0.264759   
deck            -0.026386   0.231576     -0.057449  0.155132  0.152927   
cabin_num        0.031185  -0.124038      0.045188 -0.069120 -0.079686   
side             0.017943  -0.015881      0.005226 -0.002242  0.004458   

              transported      deck  cabin_num      side  
homeplanet      -0.107755  0.230194  -0.187816  0.001179  
cryosleep       -0.404716  0.050019  -0.058838  0.001450  
destination     -0.059439  0.013535   0.003495  0.000383  
age             -0.056009  0.059463  -0.095498 -0.018635  
vip              0.032360  0.138708  -0.075954  0.009381  
roomservice      0.272828 -0.026386   0.031185  0.017943  
foodcourt        0.044451  0.231576  -0.124038 -0.015881  
shoppingmall     0.078103 -0.057449   0.045188  0.005226  
spa              0.282438  0.155132  -0.069120 -0.002242  
vrdeck           0.264759  0.152927  -0.079686  0.004458  
transported      1.000000 -0.079749   0.068027  0.093497  
deck            -0.079749  1.000000  -0.546521  0.155797  
cabin_num        0.068027 -0.546521   1.000000 -0.042179  
side             0.093497  0.155797  -0.042179  1.000000

Most notably there are no significant correlations with transported in the data besides the negative correlation with cryosleep. If we restrict the display to only correlations above 0.3 in absolute value terms we can see this fact more clearly.

In [26]:
corr: DataFrame = train_num.to_pandas().corr()
corr[np.abs(corr) >= 0.3]

homeplanet  cryosleep  destination  age  vip  roomservice  \
homeplanet           1.0        NaN          NaN  NaN  NaN          NaN   
cryosleep            NaN   1.000000          NaN  NaN  NaN          NaN   
destination          NaN        NaN          1.0  NaN  NaN          NaN   
age                  NaN        NaN          NaN  1.0  NaN          NaN   
vip                  NaN        NaN          NaN  NaN  1.0          NaN   
roomservice          NaN        NaN          NaN  NaN  NaN          1.0   
foodcourt            NaN        NaN          NaN  NaN  NaN          NaN   
shoppingmall         NaN        NaN          NaN  NaN  NaN          NaN   
spa                  NaN        NaN          NaN  NaN  NaN          NaN   
vrdeck               NaN        NaN          NaN  NaN  NaN          NaN   
transported          NaN  -0.404716          NaN  NaN  NaN          NaN   
deck                 NaN        NaN          NaN  NaN  NaN          NaN   
cabin_num            NaN        NaN          NaN  NaN  NaN          NaN   
side                 NaN        NaN          NaN  NaN  NaN          NaN   

              foodcourt  shoppingmall  spa  vrdeck  transported      deck  \
homeplanet          NaN           NaN  NaN     NaN          NaN       NaN   
cryosleep           NaN           NaN  NaN     NaN    -0.404716       NaN   
destination         NaN           NaN  NaN     NaN          NaN       NaN   
age                 NaN           NaN  NaN     NaN          NaN       NaN   
vip                 NaN           NaN  NaN     NaN          NaN       NaN   
roomservice         NaN           NaN  NaN     NaN          NaN       NaN   
foodcourt           1.0           NaN  NaN     NaN          NaN       NaN   
shoppingmall        NaN           1.0  NaN     NaN          NaN       NaN   
spa                 NaN           NaN  1.0     NaN          NaN       NaN   
vrdeck              NaN           NaN  NaN     1.0          NaN       NaN   
transported         NaN           NaN  NaN     NaN     1.000000       NaN   
deck                NaN           NaN  NaN     NaN          NaN  1.000000   
cabin_num           NaN           NaN  NaN     NaN          NaN -0.546521   
side                NaN           NaN  NaN     NaN          NaN       NaN   

              cabin_num  side  
homeplanet          NaN   NaN  
cryosleep           NaN   NaN  
destination         NaN   NaN  
age                 NaN   NaN  
vip                 NaN   NaN  
roomservice         NaN   NaN  
foodcourt           NaN   NaN  
shoppingmall        NaN   NaN  
spa                 NaN   NaN  
vrdeck              NaN   NaN  
transported         NaN   NaN  
deck          -0.546521   NaN  
cabin_num      1.000000   NaN  
side                NaN   1.0

In [27]:
corr: DataFrame = test_num.to_pandas().corr()
corr

homeplanet  cryosleep  destination       age       vip  \
homeplanet      1.000000   0.077740    -0.116908  0.031419  0.088770   
cryosleep       0.077740   1.000000     0.095332  0.053779 -0.056949   
destination    -0.116908   0.095332     1.000000  0.003799 -0.005991   
age             0.031419   0.053779     0.003799  1.000000  0.000559   
vip             0.088770  -0.056949    -0.005991  0.000559  1.000000   
roomservice     0.181243  -0.238787    -0.052787 -0.025828  0.047326   
foodcourt       0.042532  -0.202720     0.014787 -0.001124  0.121702   
shoppingmall    0.128471  -0.218817    -0.029411 -0.049426  0.027335   
spa             0.042013  -0.174148     0.012224  0.001741  0.129132   
vrdeck          0.034097  -0.172884     0.019069  0.021410  0.077932   
deck            0.199919   0.060964     0.011863  0.058774  0.121387   
cabin_num      -0.178281  -0.026658     0.006976 -0.053182 -0.084427   
side           -0.027957   0.001731    -0.003398 -0.035450  0.022210   

              roomservice  foodcourt  shoppingmall       spa    vrdeck  \
homeplanet       0.181243   0.042532      0.128471  0.042013  0.034097   
cryosleep       -0.238787  -0.202720     -0.218817 -0.174148 -0.172884   
destination     -0.052787   0.014787     -0.029411  0.012224  0.019069   
age             -0.025828  -0.001124     -0.049426  0.001741  0.021410   
vip              0.047326   0.121702      0.027335  0.129132  0.077932   
roomservice      1.000000  -0.019854      0.073770  0.018061 -0.028175   
foodcourt       -0.019854   1.000000      0.022563  0.239900  0.270965   
shoppingmall     0.073770   0.022563      1.000000  0.009608  0.023238   
spa              0.018061   0.239900      0.009608  1.000000  0.141268   
vrdeck          -0.028175   0.270965      0.023238  0.141268  1.000000   
deck             0.009151   0.234947      0.003501  0.174488  0.171682   
cabin_num       -0.014746  -0.159188     -0.027798 -0.113318 -0.119477   
side             0.001225   0.009765      0.024658 -0.014794 -0.033098   

                  deck  cabin_num      side  
homeplanet    0.199919  -0.178281 -0.027957  
cryosleep     0.060964  -0.026658  0.001731  
destination   0.011863   0.006976 -0.003398  
age           0.058774  -0.053182 -0.035450  
vip           0.121387  -0.084427  0.022210  
roomservice   0.009151  -0.014746  0.001225  
foodcourt     0.234947  -0.159188  0.009765  
shoppingmall  0.003501  -0.027798  0.024658  
spa           0.174488  -0.113318 -0.014794  
vrdeck        0.171682  -0.119477 -0.033098  
deck          1.000000  -0.591107  0.176210  
cabin_num    -0.591107   1.000000 -0.071533  
side          0.176210  -0.071533  1.000000

In [28]:
corr[np.abs(corr) >= 0.3]

homeplanet  cryosleep  destination  age  vip  roomservice  \
homeplanet           1.0        NaN          NaN  NaN  NaN          NaN   
cryosleep            NaN        1.0          NaN  NaN  NaN          NaN   
destination          NaN        NaN          1.0  NaN  NaN          NaN   
age                  NaN        NaN          NaN  1.0  NaN          NaN   
vip                  NaN        NaN          NaN  NaN  1.0          NaN   
roomservice          NaN        NaN          NaN  NaN  NaN          1.0   
foodcourt            NaN        NaN          NaN  NaN  NaN          NaN   
shoppingmall         NaN        NaN          NaN  NaN  NaN          NaN   
spa                  NaN        NaN          NaN  NaN  NaN          NaN   
vrdeck               NaN        NaN          NaN  NaN  NaN          NaN   
deck                 NaN        NaN          NaN  NaN  NaN          NaN   
cabin_num            NaN        NaN          NaN  NaN  NaN          NaN   
side                 NaN        NaN          NaN  NaN  NaN          NaN   

              foodcourt  shoppingmall  spa  vrdeck      deck  cabin_num  side  
homeplanet          NaN           NaN  NaN     NaN       NaN        NaN   NaN  
cryosleep           NaN           NaN  NaN     NaN       NaN        NaN   NaN  
destination         NaN           NaN  NaN     NaN       NaN        NaN   NaN  
age                 NaN           NaN  NaN     NaN       NaN        NaN   NaN  
vip                 NaN           NaN  NaN     NaN       NaN        NaN   NaN  
roomservice         NaN           NaN  NaN     NaN       NaN        NaN   NaN  
foodcourt           1.0           NaN  NaN     NaN       NaN        NaN   NaN  
shoppingmall        NaN           1.0  NaN     NaN       NaN        NaN   NaN  
spa                 NaN           NaN  1.0     NaN       NaN        NaN   NaN  
vrdeck              NaN           NaN  NaN     1.0       NaN        NaN   NaN  
deck                NaN           NaN  NaN     NaN  1.000000  -0.591107   NaN  
cabin_num           NaN           NaN  NaN     NaN -0.591107   1.000000   NaN  
side                NaN           NaN  NaN     NaN       NaN        NaN   1.0

If we similarly drill down in the test set correlations, we can see there are no significant correlations in the test set.All in all, these correlation matrices are pretty similar, full of low floats that don't point to any strong correlations among our variables. Let's move on to modeling.

________________________________________________________________________

# Modeling

In this section we'll try a variety of classifiers to see how well they do on this dataset before moving to more complex binary classifiers or classifier ensembles. We'll first use a TPOT (Tree-based Pipeline Optimization Tool) classifier to guess what kind of classifier might be used for our training data, before training LightGBM,XGBoost, CatBoost, and AdaBoost classifiers. The goal here is to assess how well we can predict data within the test set based on these different algorithms before moving to voting or stacking classifiers, which could help us tighten up our predictions further. 

The TPOT classifier is an autoML optimization pipeline so we will run that algorithm, while the other classifiers will use bayesian hyperparameter tuning to train more performant models before we run predictions on the test set. 

Let's start by scaling our training and test sets, as well as dividing the datasets before we dive into the models. 

In [29]:
train: DataFrame = train.drop("outliers")
test: DataFrame = test.drop("outliers")

np.nan_to_num(train_num, copy=False, nan=0.0)
np.nan_to_num(test_num, copy=False, nan=0.0)

scaled_train_num_x: NDArray = conduct_PCA(train_num.drop("transported"))
scaled_test_num_x: NDArray = conduct_PCA(test_num)

x_train, x_val, y_train, y_val = train_test_split(
    scaled_train_num_x, y, test_size=0.3, stratify=y
)


# summarize training set size
#print("Labeled train set:", x_train_lab.shape, y_train_lab.shape)
#print("Unlabeled train set:", x_test_unlab.shape, y_test_unlab.shape)
# summarize test set size
#print("Test set:", x_val.shape, y_val.shape)

## Ensemble 1: TPOT-selected classifier 

TPOT uses "genetic programming" to create and test multiple generations of pipelines. In a process inspired by natural selection/evolution, it iteratively tweaks the best performing pipelines and classifier types, passing them on to the next generation, until it identifies the top performing classifier and hyperparameter set for our data. Though we already have classifiers in mind, we can start here in the event that there is a model that we have not considered that may be useful for our data and the problem at hand. 

In [30]:
cv = RepeatedStratifiedKFold(n_splits=3, n_repeats=3, random_state=1)

model = TPOTClassifier(
    generations=3,
    population_size=50,
    cv=cv,
    scoring="accuracy",
    verbosity=2,
    random_state=15,
    n_jobs=-1,
).fit(x_train, y_train)


best_pipeline = model.fitted_pipeline_
tpot_classifier = clone(best_pipeline)
tpot_classifier_params = tpot_classifier.steps[-1][1].get_params()
tpot_classifier_name = str(type(best_pipeline.steps[-1][1])).split(".")[-1][:-2]

# Fit the new classifier on the training data
tpot_classifier.fit(training_x, training_y)
predictions = tpot_classifier.predict(validation_x)
tpot_accuracy = tpot_classifier.score(validation_x, validation_y)
print(f"\n{tpot_classifier_name} accuracy is {tpot_accuracy:.3f}")

model_stats_df = calculate_model_statistics(
    y_true=validation_y, y_predict=predictions, title=tpot_classifier_name
)

Optimization Progress:   0%|          | 0/200 [00:00<?, ?pipeline/s]


Generation 1 - Current best internal CV score: 0.7701457023498954

Generation 2 - Current best internal CV score: 0.7701457023498954

Generation 3 - Current best internal CV score: 0.7701457023498954

Best pipeline: ExtraTreesClassifier(input_matrix, bootstrap=True, criterion=gini, max_features=0.35000000000000003, min_samples_leaf=1, min_samples_split=11, n_estimators=100)

ExtraTreesClassifier accuracy is 0.784


Now that we've defined this first model, let's assess its performance across the 

## Ensemble 2: LGBM classifier

We'll next test an LGBM classifier since these models can be very accurate and fast models to use in prediction, and we also can tune the model with L1 and L2 regularization to control against overfitting if need be. 

In [32]:
params = {
    "boosting_type": ["gbdt"],
    "num_leaves": int_range(2, 15),
    "max_depth": int_range(1, 15),
    "n_estimators": np.linspace(50, 300, 10, dtype=int),
    "reg_alpha": np.linspace(0, 1, 10),
    "reg_lambda": np.linspace(0, 1, 10),
    "learning_rate": np.linspace(0.1, 1, 20),
    "subsample": np.linspace(0.1, 1, 20),
}

lgbm_params = skopt_bayesian_search(
    LGBMClassifier(verbose=-1), x_train, y_train, params
)

lgbm_classifier: LGBMClassifier = LGBMClassifier(**lgbm_params).fit(
    training_x, training_y
)
predictions: NDArray = lgbm_classifier.predict(validation_x)

lgbm_accuracy: float = lgbm_classifier.score(validation_x, validation_y)
print(f"LGBM classifier accuracy is {lgbm_accuracy:.3f}")
model_stats_df['LGBMClassifier'] = calculate_model_statistics(y_true=validation_y, y_predict=predictions)


LGBM classifier accuracy is 0.776


## Ensemble 3: CatBoost


Catbooost similarly is another gradient boosting model, and its ordered boosting method should control against overfitting as well. It also performs its own cross-validation internally, so should render reliable, reproducbile results. 

In [33]:
params = {
    "depth": int_range(4, 10),
    "learning_rate": np.linspace(0.01, 0.3, 12),
    "iterations": np.linspace(10, 100, 12, dtype=int),
    "l2_leaf_reg": int_range(1, 10),
    "border_count": np.linspace(1, 255, 12, dtype=int),
    "bagging_temperature": np.linspace(0.0, 1.0, 12),
    "random_strength": np.linspace(0.0, 1.0, 12),
}

catboost_params = skopt_bayesian_search(
    CatBoostClassifier(verbose=False), x_train, y_train, params, np=True
)

catboost_classifier: CatBoostClassifier = CatBoostClassifier(
    verbose=False, **catboost_params
).fit(training_x, training_y)

predictions: float = catboost_classifier.predict(validation_x)
catboost_accuracy: float = catboost_classifier.score(validation_x, validation_y)

print(f"CatBoost classifier accuracy is {catboost_accuracy:.3f}")
model_stats_df['CatboostClassifier'] = calculate_model_statistics(y_true=validation_y, y_predict=predictions)

CatBoost classifier accuracy is 0.781


## Ensemble 4: XGBoost

XGBoost is another standout for machine learning modeling, with built-in methods for regularization, featuring importances, and reducing overfitting. It's known to perform well across a wide array of problems, so it may be a good bet to try out on our data.

In [34]:
params = {
    "objective": ["binary:hinge", "binary:logistic"],
    "booster": ["gbtree"],
    "max_leaves": np.linspace(1, 10, 10, dtype=int),
    "max_depth": np.linspace(3, 15, 4, dtype=int),
    "grow_policy": ["depthwise"],
    "n_estimators": np.linspace(50, 100, 10, dtype=int),
    "learning_rate": np.linspace(0.01, 1, 8),
}

xgboost_params: dict = skopt_bayesian_search(XGBClassifier(), x_train, y_train, params)
xgboost_classifier: float = XGBClassifier(**xgboost_params).fit(training_x, training_y)

predictions = xgboost_classifier.predict(validation_x)

xgboost_accuracy: float = xgboost_classifier.score(validation_x, validation_y)
print(f"XGBoost classifier accuracy is {xgboost_accuracy:.3f}")
model_stats_df['XGBboostClassifier'] = calculate_model_statistics(y_true=validation_y, y_predict=predictions)

XGBoost classifier accuracy is 0.771


## Ensemble 5: Adaboost


Since AdaBoost works to build a strong classifier by training weak classifiers and iteratively decreasing their error rates, this model could be useful for us to try given that the train and test datasets are not exact substitutes for each other. Adaboost's training process might give us a resonably performant model because of its flexibility during the fitting process.

In [35]:
from sklearn.ensemble import AdaBoostClassifier

params = {
    "n_estimators": np.linspace(35, 150, 50, dtype=int),
    "learning_rate": np.linspace(0.01, 0.3, 12),
}

adaboost_params = skopt_bayesian_search(
    AdaBoostClassifier(algorithm="SAMME"), x_train, y_train, params, np=True
)
adaboost_classifier: AdaBoostClassifier = AdaBoostClassifier(
    algorithm="SAMME", **adaboost_params
).fit(training_x, training_y)

predictions = adaboost_classifier.predict(validation_x)
adaboost_accuracy: float = adaboost_classifier.score(validation_x, validation_y)
print(f"AdaBoost classifier accuracy is {adaboost_accuracy:.3f}")
model_stats_df['AdaboostClassifier'] = calculate_model_statistics(y_true=validation_y, y_predict=predictions)

AdaBoost classifier accuracy is 0.757


We've seen a good number of ensembles so far, let's take stock of how these models have done thus far on the training and test predictions.

In [36]:
classifier_df = pd.DataFrame(
    data={
        "validation accuracy": [
            tpot_accuracy,
            lgbm_accuracy,
            catboost_accuracy,
            xgboost_accuracy,
            adaboost_accuracy,
        ],
        "test accuracy": [0.23731, 0.31470, 0.29143, 0.36988, 0.24807],
    }
).T

classifier_df.columns = [
    tpot_classifier_name,
    "LGBM",
    "Catboost",
    "XGBoost",
    "AdaBoost",
]
classifier_df

ExtraTreesClassifier      LGBM  Catboost   XGBoost  \
validation accuracy              0.783742  0.776074  0.780675  0.771472   
test accuracy                    0.237310  0.314700  0.291430  0.369880   

                     AdaBoost  
validation accuracy  0.756902  
test accuracy        0.248070

So far, our models are burning a lot of resources to perform pretty poorly. Though these are all ensembles that run different algorithms in order to arrive at their predictions, their accuracy is floating in the 76-78% range on the training set, with terrible performance on the test predictions. The ExtraTrees, LGBM, and XGBoost classifiers typically hedge against model overfitting, which would mean either that our models are misspecified for this data, or our training data isn't a good stand-in for the data that we'd like to predict on. 

Let's print out our overall model stats to take a closer look. 

In [37]:
model_stats_df

ExtraTreesClassifier  LGBMClassifier  CatboostClassifier  \
accuracy                         0.783742        0.776074            0.780675   
precision                        0.767374        0.788321            0.791297   
recall                           0.810039        0.750579            0.758301   
f_score                          0.767374        0.788321            0.791297   
false_negative_rate              0.094325        0.123850            0.120015   
false_positive_rate              0.121933        0.100077            0.099310   

                     XGBboostClassifier  AdaboostClassifier  
accuracy                       0.771472            0.756902  
precision                      0.783455            0.738284  
recall                         0.745946            0.790734  
f_score                        0.783455            0.738284  
false_negative_rate            0.126150            0.103911  
false_positive_rate            0.102377            0.139187

So far the catboost classifier is performance across the first four metrics, with our lowest false positive rate being found with our LGBM classifier. Let's try voting and stacking classifiers to see if we can salvage predictive power in the event that these models might all be weak classifiers, but weak on different subsets of the data. If that were true, we'd be able to use stacking and/or voting to create an ensemble of ensembles that is strong than any single ensemble model in isolation. 

## Ensemble 6: Voting Classifier

In [38]:
from sklearn.ensemble import VotingClassifier
from lightgbm import LGBMClassifier

lgbm = LGBMClassifier(**lgbm_params)
cat = CatBoostClassifier(**catboost_params, verbose=False)
ada = AdaBoostClassifier(**adaboost_params, algorithm="SAMME")
xgb = XGBClassifier(**xgboost_params)


voting = VotingClassifier(
    estimators=[
        ("tpot", tpot_classifier),
        ("lgbm", lgbm),
        ("catboost", cat),
        ("ada", ada),
        ("xgb", xgb),
    ],
    voting="hard",
)
voting.fit(training_x, training_y)
predictions = voting.predict(validation_x)
classifier_df["Voting"] = [voting.score(validation_x, validation_y), 0.22235]
model_stats_df['VotingClassifier'] = calculate_model_statistics(y_true=validation_y, y_predict=predictions)

## Ensemble 7: Stacking Classifier


In [39]:
lgbm = LGBMClassifier(**lgbm_params)
cat = CatBoostClassifier(**catboost_params, verbose=False)
ada = AdaBoostClassifier(**adaboost_params)
xgb = XGBClassifier(**xgboost_params)
lr = LogisticRegression()


stack = StackingClassifier(
    classifiers=[tpot_classifier, lgbm, cat, ada, xgb],
    meta_classifier=lr,
    use_probas=True,
    use_features_in_secondary=True,
).fit(training_x, training_y)

predictions = stack.predict(validation_x)

classifier_df["Stacking"] = [voting.score(validation_x, validation_y), 0.46574]
model_stats_df['StackingClassifier'] = calculate_model_statistics(y_true=validation_y, y_predict=predictions)


Now that we've trained voting and stacking classifiers, let's print out our classifier dataframe once again. 

In [40]:
classifier_df

ExtraTreesClassifier      LGBM  Catboost   XGBoost  \
validation accuracy              0.783742  0.776074  0.780675  0.771472   
test accuracy                    0.237310  0.314700  0.291430  0.369880   

                     AdaBoost    Voting  Stacking  
validation accuracy  0.756902  0.783359  0.783359  
test accuracy        0.248070  0.222350  0.465740

In [41]:
model_stats_df

ExtraTreesClassifier  LGBMClassifier  CatboostClassifier  \
accuracy                         0.783742        0.776074            0.780675   
precision                        0.767374        0.788321            0.791297   
recall                           0.810039        0.750579            0.758301   
f_score                          0.767374        0.788321            0.791297   
false_negative_rate              0.094325        0.123850            0.120015   
false_positive_rate              0.121933        0.100077            0.099310   

                     XGBboostClassifier  AdaboostClassifier  VotingClassifier  \
accuracy                       0.771472            0.756902          0.783359   
precision                      0.783455            0.738284          0.789223   
recall                         0.745946            0.790734          0.769112   
f_score                        0.783455            0.738284          0.789223   
false_negative_rate            0.126150            0.103911          0.114647   
false_positive_rate            0.102377            0.139187          0.101994   

                     StackingClassifier  
accuracy                       0.765337  
precision                      0.755423  
recall                         0.779923  
f_score                        0.755423  
false_negative_rate            0.109279  
false_positive_rate            0.125383

Our idea to try ensembles of ensembles wasn't totally off-base, but we didn't do much better. The key difference between the voting and stacking classifiers is that the voting classifier holds the estimators in parallel, deciding off the majority "vote" between, whereas the stacking classifier uses the estimators in a chain, refining the predictions of the previous step. Considering that this incremental improvement is also how the AdaBoost algorithm trains successive decision trees, I think that it's safe to say that we're hitting an upper limit on how far we can get using supervised learning techniques here. Let's recreate our outlier plot from earlier in case we can use the decision scores to glean any further insight into what's going on in the data.  

In [42]:
outlier_plot.show()

In light of what we've seen in our models just now, the difference between these two datasets is rather stark--the test data is sampled from a different distribution, and also has a much larger spread of outliers as well. Our models are probably only accurately predicting observations in the 0-2.5 decision score range. Let's look into K Nearest Neighbors and Label Spreading classifiers--we may be able to map wide clusters that contain upper and lower range observations, which would help us bridge the gap between the domains of the training and test sets!

# Unsupervised learning methods
## K Nearest Neighbors

In [43]:
params = {
    "n_neighbors": int_range(1, 25),
    "weights": ["uniform", "distance"],
    "algorithm": ["auto", "ball_tree", "kd_tree", "brute"],
    "p": [1, 1.5, 2],
}

knn_params = skopt_bayesian_search(
    KNeighborsClassifier(n_jobs=-1), x_train, y_train, params
)
knn_classifier: KNeighborsClassifier = KNeighborsClassifier(**knn_params).fit(
    training_x, training_y
)

knn_predictions: NDArray = knn_classifier.predict(x_test)
knn_accuracy: float = knn_classifier.score(validation_x, validation_y)

classifier_df["knn"] = [knn_accuracy, 0.25298]

## Label Spreading

In [44]:

x_train, x_val, y_train, y_val = train_test_split(
    scaled_train_num_x, y, test_size=0.3, stratify=y
)

x_train_lab, x_train_unlab, y_train_lab, y_train_unlab = train_test_split(
    x_train, y_train, test_size=0.5, random_state=1, stratify=y_train
)

x_train_mixed: NDArray = np.concatenate((x_train_lab, x_train_unlab))

# create "no label" pool for unlabeled data
nolabel: list[int] = [-1 for _ in range(len(y_train_unlab))]
y_train_mixed: NDArray = np.concatenate((y_train_lab, nolabel))

Now that we've mixed labeled and unlabeled data, we can run multiple iterations of this classifier to identify which version of the model is most accurate. We'll use the knn kernel here.

In [45]:
accuracy_scores = dict()

for n in range(1, 30):
    model = LabelSpreading(kernel="knn", n_neighbors=n, n_jobs=-1)
    model.fit(x_train_mixed, y_train_mixed)

    predictions: NDArray = model.predict(x_val)

    score: float = accuracy_score(y_val, predictions)
    accuracy_scores[n] = score

label_spreading_performance = pd.DataFrame()
label_spreading_performance["n_neighbors"] = accuracy_scores.keys()
label_spreading_performance["accuracy"] = accuracy_scores.values()
label_spreading_performance.set_index("n_neighbors", inplace=True)

print(
    f"Highest accuracy of {label_spreading_performance.accuracy.max():.3f} found at n = {label_spreading_performance.accuracy.idxmax()} neighbors"
)

Highest accuracy of 0.744 found at n = 16 neighbors


When we ran fitted classifiers for different values of k, 19 neighbors gave us the highest accuracy score within the validation set. But not so fast.

Even though we've found that the model is most accurate on the training set when the n_neighbors parameter is set to that value, that level of accuracy on the training set isn't the problem that we're trying to solve. Therefore, we could expect clusters for these higher values to be far and above of the "known" clusters we determined in the training set--a test set datapoint might only have 1 or two points within a cluster to compare too, so we should set n_neighbors as low as possible so that the algorithm has something to latch onto to make a more accurate prediction. So let's set n_neighbors equal to one instead. That lower accuracy up front might translate to higher test set accuracy instead.

In [46]:
LS_classifier = LabelSpreading(kernel="knn", n_neighbors=1, n_jobs=-1)

LS_classifier.fit(x_train_mixed, y_train_mixed)

predictions: NDArray = LS_classifier.predict(x_val)
LS_accuracy: float = accuracy_score(y_val, predictions)

# make predictions on test set
LS_predictions: NDArray = LS_classifier.predict(scaled_test_num_x)

classifier_df["LabelSpreading"] = [LS_accuracy, 0.67593]
classifier_df

ExtraTreesClassifier      LGBM  Catboost   XGBoost  \
validation accuracy              0.783742  0.776074  0.780675  0.771472   
test accuracy                    0.237310  0.314700  0.291430  0.369880   

                     AdaBoost    Voting  Stacking      knn  LabelSpreading  
validation accuracy  0.756902  0.783359  0.783359  0.76227        0.582439  
test accuracy        0.248070  0.222350  0.465740  0.25298        0.675930

Though training set accuracy is now much lower on the training set, this model configuration received an accuracy score of 0.67523 on the test data, proving out our intuition in sacrificing accuracy up front for higher accuracy later. The Label Spreading Classifier is the high water mark for test predictions so far, which is a much cheaper model to train and run compared the ensembles we were working with before. Nonetheless, this performance isn't strong enough, we can do better. The starter notebook for the Kaggle competition uses a tensorflow random forest, which outperforms our Label Spreading frontrunner out of the box. Let's see if we can get more performance out it with some hyperparameter tuning. 